In [1]:
import numpy as np
import pandas as pd
import altair as alt
import warnings


from datetime import datetime

# disable MaxRow error in Altair
alt.data_transformers.disable_max_rows() 

# ignore warnings
warnings.filterwarnings("ignore")

# Data Preprocessing

In [2]:
# read in dataset
gps = pd.read_csv('googleplaystore.csv')

# listwise deletion of missing values
gps_clean = gps.dropna()

# Reviews: convert to int64
gps_clean.loc[:,'Reviews'] = pd.to_numeric(gps_clean['Reviews'])

# Size: convert to float64 and standardize to megabtyes
# any sizes that are non-numeric are defaulted to NaN
def scale_to_mb(element):
    if element[-1] == "M":
        return float(element[:-1])
    elif element[-1] == "k":
        return float(element[:-1])/1000
    else:
        return -1
gps_clean.loc[:,"Size"] = [scale_to_mb(i) for i in gps_clean['Size']]
gps_clean = gps_clean[gps_clean['Size'] != -1]

# Price: remove characters and convert to float64
gps_clean.loc[:,'Price'] = [float(element.replace('$','')) for element in gps_clean['Price']]

# Installs: remove characters and convert to int64
gps_clean.loc[:,'Installs'] = [int(i.replace(',', '').replace('+','')) for i in gps_clean['Installs']]

# new Install_Percentile column, install count binned into 4 quartiles
bin_labels = ['4th', '3rd', '2nd', '1st']
gps_clean.loc[:,'Install_Percentile'] = pd.qcut(gps_clean['Installs'], q=4, labels=bin_labels)

# Last Updated: change to number of days since last update, makes it a hard count instead of abstract date
# start point will be entry with most recent date, then counting back from there
gps_clean.loc[:,'Last Updated'] = [datetime.strptime(i, '%B %d, %Y') for i in gps_clean['Last Updated']]
gps_clean.loc[:,'Days Since Update'] = [abs((pd.Timestamp(2018,9,4,0)- i).days) for i in gps_clean['Last Updated']]

# drop columns
gps_clean.drop(columns=['Genres', 'Android Ver', 'Current Ver', 'Last Updated'], inplace=True)

# drop duplicate rows
gps_clean = gps_clean.drop_duplicates()

# group by App name, sort by reviews
sorted_gps = gps_clean.groupby(['App']).apply(lambda x: x.sort_values(["Reviews"])).reset_index(drop=True)
sorted_gps.index.name = None

# delete entries with duplicate App names but keep one with most Reviews
gps_clean = sorted_gps.drop_duplicates(subset='App', keep='last')

## EDA

In [3]:
# view first 5 entries of dataset
gps_clean.head()

App            Category  Rating  Reviews    Size  \
0  +Download 4 Instagram Twitter              SOCIAL     4.5    40467  22.000   
1     - Free Comics - Comic Apps              COMICS     3.5      115   9.100   
2                             .R               TOOLS     4.5      259   0.203   
3                         /u/app       COMMUNICATION     4.7      573  53.000   
4                         058.ba  NEWS_AND_MAGAZINES     4.4       27  14.000   

   Installs  Type  Price Content Rating Install_Percentile  Days Since Update  
0   1000000  Free    0.0       Everyone                2nd                 33  
1     10000  Free    0.0     Mature 17+                4th                 53  
2     10000  Free    0.0       Everyone                4th               1449  
3     10000  Free    0.0     Mature 17+                4th                 63  
4       100  Free    0.0       Everyone                4th                 60

In [4]:
# basic info about dataset
gps_clean.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 7023 entries, 0 to 7417
Data columns (total 11 columns):
App                   7023 non-null object
Category              7023 non-null object
Rating                7023 non-null float64
Reviews               7023 non-null int64
Size                  7023 non-null float64
Installs              7023 non-null int64
Type                  7023 non-null object
Price                 7023 non-null float64
Content Rating        7023 non-null object
Install_Percentile    7023 non-null category
Days Since Update     7023 non-null int64
dtypes: category(1), float64(3), int64(3), object(4)
memory usage: 610.6+ KB


In [5]:
# numerical summary of numeric variables
gps_clean.describe()

Rating       Reviews         Size      Installs        Price  \
count  7023.000000  7.023000e+03  7023.000000  7.023000e+03  7023.000000   
mean      4.160743  1.451567e+05    21.764210  4.480581e+06     1.172038   
std       0.559197  1.024515e+06    22.730334  2.715075e+07    18.202232   
min       1.000000  1.000000e+00     0.008500  1.000000e+00     0.000000   
25%       4.000000  8.400000e+01     4.900000  1.000000e+04     0.000000   
50%       4.300000  1.553000e+03    13.000000  1.000000e+05     0.000000   
75%       4.500000  2.670450e+04    31.000000  1.000000e+06     0.000000   
max       5.000000  4.489389e+07   100.000000  1.000000e+09   400.000000   

       Days Since Update  
count        7023.000000  
mean          327.378186  
std           425.740680  
min            27.000000  
25%            52.000000  
50%           131.000000  
75%           435.500000  
max          3028.000000

In [6]:
# scatterplot matrix between numeric variables
alt.Chart(gps_clean).mark_circle(size=10).encode(
    alt.X(alt.repeat("column"), type='quantitative'),
    alt.Y(alt.repeat("row"), type='quantitative'),
    opacity=alt.value(0.2),
    color=alt.value('red')
).properties(
    width=150,
    height=150
).repeat(
    row=['Reviews', 'Rating', 'Size', 'Price', 'Days Since Update'],
    column=['Days Since Update', 'Price', 'Size', 'Rating', 'Reviews']
).configure_title(fontSize=18).configure_axis(
    labelFontSize=14,
    titleFontSize=20
)

alt.RepeatChart(...)

## Free or Paid?

In [7]:
# layered histogram: Log Installs and Type
source = gps_clean.copy()
source.loc[:,'log_Installs'] = np.log(source['Installs'])

brush = alt.selection(type='interval')
base = alt.Chart(source).add_selection(brush)

alt.Chart(source, title='Paid vs Free: Log Install Count').transform_fold(
    ['Free', 'Paid']
).mark_area(
    opacity=0.5,
    interpolate='step'
).encode(
    alt.X('log_Installs:Q', axis=alt.Axis(title='Log Installs'), bin=alt.Bin(maxbins=30)),
    alt.Y('count()', axis=alt.Axis(title='Count of Apps'), stack=None),
    alt.Color('Type')
).configure_title(fontSize=18).configure_axis(
    labelFontSize=16,
    titleFontSize=16
).configure_legend(titleFontSize=14, labelFontSize=12)

alt.Chart(...)

## Category?

In [8]:
# barchart showing number of apps within each category, color by Install_Percentile
alt.Chart(gps_clean, title='Number of Apps within Category').mark_bar().encode(
    x=alt.X('Category', axis=alt.Axis(title='Category', labelAngle=-45), sort='-y'),
    y=alt.Y('count()', axis=alt.Axis(title='Number of Apps')),
    color=alt.Color('Install_Percentile', title='Install Percentile')
).configure_title(fontSize=18).configure_axis(
    labelFontSize=12,
    titleFontSize=16
).configure_legend(titleFontSize=14, labelFontSize=12)

alt.Chart(...)

In [9]:
# proportion of apps in 1st install percentile to total apps per category
gps_1stq = gps_clean[(gps_clean['Install_Percentile']=='1st') | (gps_clean['Install_Percentile']=='2nd') ]
proportion_50 = gps_1stq['Category'].value_counts()/gps_clean['Category'].value_counts()
(proportion_50).sort_values(ascending=False)

ENTERTAINMENT          0.803571
EDUCATION              0.675325
GAME                   0.644336
PHOTOGRAPHY            0.637255
SHOPPING               0.623288
WEATHER                0.600000
HOUSE_AND_HOME         0.571429
VIDEO_PLAYERS          0.522124
FOOD_AND_DRINK         0.513889
HEALTH_AND_FITNESS     0.492147
COMMUNICATION          0.468085
SPORTS                 0.466063
SOCIAL                 0.442308
PRODUCTIVITY           0.439462
TRAVEL_AND_LOCAL       0.432624
MAPS_AND_NAVIGATION    0.404255
PERSONALIZATION        0.401460
FAMILY                 0.391699
NEWS_AND_MAGAZINES     0.363636
DATING                 0.360656
TOOLS                  0.354067
BOOKS_AND_REFERENCE    0.319149
PARENTING              0.318182
LIFESTYLE              0.301115
COMICS                 0.297872
BEAUTY                 0.297297
AUTO_AND_VEHICLES      0.285714
FINANCE                0.275194
LIBRARIES_AND_DEMO     0.266667
ART_AND_DESIGN         0.250000
BUSINESS               0.216216
EVENTS  

## Download Size and Install Count

In [10]:
# boxplot: File Size and Install Percentile
alt.Chart(gps_clean, title='BoxPlot: Install Percentile vs Size').mark_boxplot(extent='min-max').encode(
    x=alt.X('Install_Percentile', axis=alt.Axis(title='Install Percentile')),
    y=alt.Y('Size'),
    color=alt.Color('Install_Percentile', legend=None)
).configure_title(fontSize=18).configure_axis(
    labelFontSize=16,
    titleFontSize=16
).properties(width=200)

alt.Chart(...)

## Rating and Install Count

In [11]:
# histogram: Rating and Install Percentile
alt.Chart(gps_clean, title='Rating and Install Percentile').mark_bar().encode(
    x=alt.X('Rating', axis=alt.Axis(title='Rating')),
    y=alt.Y('count()', axis=alt.Axis(title='Number of Apps'), sort='-x'),
    color=alt.Color('Install_Percentile', title='Install Percentile')
).configure_title(fontSize=18).configure_axis(
    labelFontSize=12,
    titleFontSize=16
).configure_legend(titleFontSize=14, labelFontSize=12)

alt.Chart(...)

In [12]:
# check average number of reviews for perfect scores
np.mean(gps_clean[gps_clean['Rating']==5]['Reviews'])

8.428571428571429

# Modeling

## Outliers

In [13]:
def winsorize(data, variables, k=0):
    """
    Input:
      data (data frame): the table to be filtered
      variable (list): the names of the column with numerical outliers
      k (integer): the number of observations to replace
    
    Output:
      a winsorized data frame with the k outliers (smallest and largest values) replaced.
      
    Note: This function should not change the contents of data.
    """
    # Make a copy() of the data so not to change the original dataframe
    data_copy = data.copy()
    
    # Sort the values of the given variable to find the replacement values
    for i in variables: 
        sorted_val = np.sort(data[i])
        lower = sorted_val[k]
        upper = sorted_val[-(k+1)]

        ## Replace outliers on data_copy
        data_copy.loc[(data_copy[i] > upper), i] = upper
        data_copy.loc[(data_copy[i] < lower), i] = lower

    return data_copy


# new dataset for clean and winsorized data
gps_winsorized = winsorize(gps_clean, ['Reviews', 'Rating', 'Size', 'Price', 'Days Since Update'], 100)

## Numeric Encoding

In [14]:
# remove App, Installs, and Type from data for modeling
gps_winsorized.drop(columns=['App', 'Installs', 'Type'], inplace=True)

# encode Category, Content Rating, and Install_Percentiles to numeric categories
gps_winsorized["Category"] = gps_winsorized["Category"].astype('category').cat.codes
gps_winsorized["Install_Percentile"] = gps_winsorized["Install_Percentile"].astype('category').cat.codes
gps_winsorized["Content Rating"] = gps_winsorized["Content Rating"].astype('category').cat.codes

In [15]:
gps_winsorized.head()

Category  Rating  Reviews    Size  Price  Content Rating  \
0        27     4.5    40467  22.000    0.0               1   
1         5     3.5      115   9.100    0.0               3   
2        29     4.5      259   0.292    0.0               1   
3         6     4.7      573  53.000    0.0               3   
4        21     4.4       27  14.000    0.0               1   

   Install_Percentile  Days Since Update  
0                   2                 33  
1                   0                 53  
2                   0               1449  
3                   0                 63  
4                   0                 60

In [16]:
gps_winsorized.shape

(7023, 8)

## Ordered Logistic Regression

In [17]:
from sklearn.model_selection import train_test_split

# separate predictors and response
predictors = gps_winsorized.drop(columns=['Install_Percentile'])
response = gps_winsorized['Install_Percentile']

# download mord package for ordered logistic regression

In [18]:
pip install mord

Processing /home/jovyan/.cache/pip/wheels/80/1d/8a/bef1a01b6a3c91494905d161d5426c181819f9730a773141eb/mord-0.6-py3-none-any.whl
Note: you may need to restart the kernel to use updated packages.


In [ ]:
from mord import LogisticAT
from sklearn.metrics import accuracy_score
from sklearn.model_selection import cross_val_score
from sklearn.metrics import make_scorer

# create accuracy scorer
def acc_function(true, fit):
    fit = np.round(fit)
    fit.astype('int')
    return accuracy_score(true, fit)
acc = make_scorer(acc_function)

# fit ordered logistic model, alpha set for no regularization
model_ordinal = LogisticAT(alpha=0)

acc_ordinal = cross_val_score(model_ordinal,
    predictors,
    response,
    cv=5,
    scoring=acc)
print('Ordered Logistic Regression Accuracy: ', np.mean(acc_ordinal))